In [1]:
import random

import pandas as pd

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

from tensorflow import keras
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.constraints import unit_norm

from matplotlib import pyplot as plt

In [2]:
def loadNBAData():
    raw_data = pd.read_csv('./convertcsv.csv', sep=',')
    raw_data = raw_data.sample(frac = 1)
    results = raw_data.pop('WL')
    results_final = results.map(lambda x: 1 if x == 'W' else 0)
    data_cleaned = raw_data.drop(columns=['SEASON_YEAR', 'TEAM_ID', 'GAME_ID', 'TEAM_ABBREVIATION', 'TEAM_NAME', 'MATCHUP', 'GAME_DATE', 'MIN'])
    data_final = data_cleaned.filter(regex='.*(?<!RANK)$')
    
    return (data_final, results_final)

In [3]:
(data_final, results_final) = loadNBAData()
data_final.head()

FGM  FGA  FG_PCT  FG3M  FG3A  FG3_PCT  FTM  FTA  FT_PCT  OREB  ...  REB  \
1140   25   48   0.521     8    16    0.500    4    5   0.800     7  ...   19   
1363   12   44   0.273     4    20    0.200    7    9   0.778     3  ...   23   
500    24   47   0.511     5    17    0.294    8   10   0.800     4  ...   21   
784    23   47   0.489     5    16    0.313    6    7   0.857     6  ...   25   
1295   23   51   0.451     4    14    0.286    8   12   0.667    12  ...   31   

      AST  TOV  STL  BLK  BLKA  PF  PFD  PTS  PLUS_MINUS  
1140   13    6    3    2     2   5    5   62          -1  
1363    7    6    3    1     1   5    6   35         -17  
500    15    6    6    2     3   8    9   61           0  
784    14    8    3    1     2   4    6   57           2  
1295   12    9    3    3     4  11    7   58           5  

[5 rows x 21 columns]

In [4]:
# 1 - win, 0 - loss
results_final.head()

1140    1
1363    0
500     0
784     1
1295    1
Name: WL, dtype: int64

In [5]:
def getModelAccuracy(featuresUsed):
    # get an array of indexes of True values, eg for [True, False, True] get [0, 2]
    remainingFeatures = [x for x in range(len(featuresUsed)) if featuresUsed[x]]
    data_final__ = data_final.iloc[:, remainingFeatures]
    
    # create model
    X_train, X_test, y_train, y_test = train_test_split(data_final__, results_final, test_size=0.33, random_state=7, stratify=results_final)
    scaler = StandardScaler()
    scaler.fit(X_train)
    X_train = scaler.transform(X_train)
    X_test = scaler.transform(X_test)
    
    model = Sequential()
    model.add(Dense(input_dim=X_train.shape[1], units=500, activation='relu', kernel_constraint=unit_norm()))
    model.add(Dropout(rate=0.2))
    model.add(Dense(units=100, activation='relu', kernel_constraint=unit_norm()))
    model.add(Dense(units=1, activation='sigmoid'))
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    
    history = model.fit(X_train, y_train, batch_size=64, epochs=20, verbose=1, validation_split=0.3)
    return history.history['val_accuracy'][-1]

In [6]:
class Individual():
    
    def __init__(self, numResources):
        # code is a binary array where 0 represents the absence of a feature
        self.code = [random.random() < 0.5 for _ in range(numResources)]
        self.correctNonFeasible()
        
        self.fitness = self.calculateFitness()
        
    def __lt__(self, other):
        if (self.fitness == other.fitness):
            # the smaller the code, the better (less features)
            return len([x for x in self.code if x]) < len([x for x in other.code if x])
        
        # a better individual has a higher accuracy
        return self.fitness > other.fitness
        
    def invert(self):
        i = random.randrange(len(self.code))
        self.code[i] = not self.code[i]
        if self.isFeasible():
            return i
        return -1
    
    def isFeasible(self):
        for c in self.code:
            if c:
                return True
        return False
        
    def correctNonFeasible(self):
        for c in self.code:
            if c:
                return
        # at least one feature must be present
        index = random.randrange(0, len(self.code))
        self.code[index] = True
        
    def calculateFitness(self):
        return getModelAccuracy(self.code)

In [7]:
def selection(population):
    TOURNAMENT_SIZE = 6
    maxAccuracy = float('-inf')
    bestIndex = -1
    
    for i in range(TOURNAMENT_SIZE):
        index = random.randrange(len(population))
        if population[index].fitness > maxAccuracy:
            maxAccuracy = population[index].fitness
            bestIndex = index
    
    return bestIndex

In [8]:
def crossover(parent1, parent2, child1, child2):
    breakpoint = random.randrange(0, len(parent1.code))
    
    child1.code[:breakpoint] = parent1.code[:breakpoint]
    child2.code[:breakpoint] = parent2.code[:breakpoint]
    
    child1.code[breakpoint:] = parent2.code[breakpoint:]
    child2.code[breakpoint:] = parent1.code[breakpoint:]
    
    child1.correctNonFeasible()
    child2.correctNonFeasible()

In [9]:
def mutation(individual):
    MUTATION_PROB = 0.05
    for i in range(len(individual.code)):
        if random.random() < MUTATION_PROB:
            individual.code[i] = not individual.code[i]
            
    individual.correctNonFeasible()

In [10]:
def simulatedAnnealing(individual, iters):
    for i in range(iters):
        j = individual.invert()
        if j < 0:
            continue
        newFitness = individual.calculateFitness()
        
        if newFitness > individual.fitness:
            individual.fitness = newFitness
        else:
            p = 1.0 / (i + 1) ** 0.5
            q = random.uniform(0, 1)
            if p < q:
                individual.fitness = newFitness
            else:
                individual.code[j] = not individual.code[j]

In [56]:
def genAlgWithoutSimulatedAnnealing(n):
    POPULATION_SIZE = 10
    numResources = n #data_final.shape[1]
    population = [Individual(numResources) for i in range(POPULATION_SIZE)]
    newPopulation = [Individual(numResources) for i in range(POPULATION_SIZE)]

    ELITISM_SIZE = int(0.3 * POPULATION_SIZE)
    MAX_ITER = 15
    for i in range(MAX_ITER):
        population.sort()
        newPopulation[:ELITISM_SIZE] = population[:ELITISM_SIZE]
        for j in range(ELITISM_SIZE, POPULATION_SIZE-1, 2):
            parent1Index = selection(population)
            parent2Index = selection(population)
            
            crossover(population[parent1Index], population[parent2Index], newPopulation[j], newPopulation[j+1])

            mutation(newPopulation[j])
            mutation(newPopulation[j+1])

            newPopulation[j].fitness = newPopulation[j].calculateFitness()
            newPopulation[j + 1].fitness = newPopulation[j + 1].calculateFitness()

        population = newPopulation

    bestIndividual = max(population, key=lambda x: x.fitness)
    print('Solution: {}, fitness: {}'.format(bestIndividual.code, bestIndividual.fitness))

In [48]:
def genAlgSimulatedAnnealing():
    POPULATION_SIZE = 15
    numResources = 10 #data_final.shape[1]
    population = [Individual(numResources) for i in range(POPULATION_SIZE)]
    newPopulation = [Individual(numResources) for i in range(POPULATION_SIZE)]

    ELITISM_SIZE = int(0.3 * POPULATION_SIZE)
    MAX_ITER = 20
    for i in range(MAX_ITER):
        population.sort()
        newPopulation[:ELITISM_SIZE] = population[:ELITISM_SIZE]
        for j in range(ELITISM_SIZE, POPULATION_SIZE-1, 2):
            parent1Index = selection(population)
            parent2Index = selection(population)

            crossover(population[parent1Index], population[parent2Index], newPopulation[j], newPopulation[j+1])

            mutation(newPopulation[j])
            mutation(newPopulation[j+1])

            newPopulation[j].fitness = newPopulation[j].calculateFitness()
            newPopulation[j + 1].fitness = newPopulation[j + 1].calculateFitness()


        simulatedAnnealing(newPopulation[0], 10)
        population = newPopulation

    bestIndividual = max(population, key=lambda x: x.fitness)
    print('Solution: {}, fitness: {}'.format(bestIndividual.code, bestIndividual.fitness))

In [49]:
genAlgSimulatedAnnealing()

Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.7251 - accuracy: 0.5227 - val_loss: 0.7106 - val_accuracy: 0.5356
Epoch 2/20
16/16 [==============================] - 0s 2ms/step - loss: 0.7013 - accuracy: 0.5395 - val_loss: 0.7088 - val_accuracy: 0.5264
Epoch 3/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7061 - accuracy: 0.5247 - val_loss: 0.6927 - val_accuracy: 0.5540
Epoch 4/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6927 - accuracy: 0.5356 - val_loss: 0.7143 - val_accuracy: 0.5609
Epoch 5/20
16/16 [==============================] - 0s 2ms/step - loss: 0.7065 - accuracy: 0.5494 - val_loss: 0.7029 - val_accuracy: 0.5356
Epoch 6/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6978 - accuracy: 0.5593 - val_loss: 0.6946 - val_accuracy: 0.5310
Epoch 7/20
16/16 [==============================] - 0s 2ms/step - loss: 0.7011 - accuracy: 0.5267 - val_loss: 0.6916 - val_accuracy: 0.5379
Epoch 8/20
16/16 [==

16/16 [==============================] - 0s 2ms/step - loss: 0.5473 - accuracy: 0.7144 - val_loss: 0.6421 - val_accuracy: 0.6391
Epoch 20/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5436 - accuracy: 0.7194 - val_loss: 0.6515 - val_accuracy: 0.6115
Epoch 1/20
16/16 [==============================] - 1s 8ms/step - loss: 0.7207 - accuracy: 0.5425 - val_loss: 0.7048 - val_accuracy: 0.5241
Epoch 2/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6833 - accuracy: 0.5455 - val_loss: 0.7606 - val_accuracy: 0.5241
Epoch 3/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6943 - accuracy: 0.5721 - val_loss: 0.7151 - val_accuracy: 0.4943
Epoch 4/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6891 - accuracy: 0.5899 - val_loss: 0.7116 - val_accuracy: 0.5195
Epoch 5/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6783 - accuracy: 0.5949 - val_loss: 0.7077 - val_accuracy: 0.4897
Epoch 6/20
16/16 [============

16/16 [==============================] - 0s 2ms/step - loss: 0.6318 - accuracy: 0.6413 - val_loss: 0.6343 - val_accuracy: 0.6575
Epoch 18/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6224 - accuracy: 0.6453 - val_loss: 0.6264 - val_accuracy: 0.6460
Epoch 19/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6196 - accuracy: 0.6413 - val_loss: 0.6291 - val_accuracy: 0.6575
Epoch 20/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6190 - accuracy: 0.6443 - val_loss: 0.6309 - val_accuracy: 0.6644
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6745 - accuracy: 0.6018 - val_loss: 0.6447 - val_accuracy: 0.6437
Epoch 2/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6491 - accuracy: 0.6453 - val_loss: 0.6329 - val_accuracy: 0.6506
Epoch 3/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6258 - accuracy: 0.6334 - val_loss: 0.6274 - val_accuracy: 0.6575
Epoch 4/20
16/16 [==========

16/16 [==============================] - 0s 3ms/step - loss: 0.5787 - accuracy: 0.6947 - val_loss: 0.6452 - val_accuracy: 0.6575
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5712 - accuracy: 0.6957 - val_loss: 0.6213 - val_accuracy: 0.6414
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5660 - accuracy: 0.6986 - val_loss: 0.6285 - val_accuracy: 0.6437
Epoch 18/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5583 - accuracy: 0.6937 - val_loss: 0.6246 - val_accuracy: 0.6460
Epoch 19/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5539 - accuracy: 0.7045 - val_loss: 0.6313 - val_accuracy: 0.6529
Epoch 20/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5530 - accuracy: 0.7144 - val_loss: 0.6393 - val_accuracy: 0.6414
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.7033 - accuracy: 0.5603 - val_loss: 0.6790 - val_accuracy: 0.5724
Epoch 2/20
16/16 [========

16/16 [==============================] - 0s 3ms/step - loss: 0.5878 - accuracy: 0.6709 - val_loss: 0.6691 - val_accuracy: 0.6299
Epoch 14/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5921 - accuracy: 0.6650 - val_loss: 0.6565 - val_accuracy: 0.6437
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5874 - accuracy: 0.6640 - val_loss: 0.6529 - val_accuracy: 0.6437
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5843 - accuracy: 0.6640 - val_loss: 0.6744 - val_accuracy: 0.6437
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5793 - accuracy: 0.6789 - val_loss: 0.6599 - val_accuracy: 0.6276
Epoch 18/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5830 - accuracy: 0.6789 - val_loss: 0.6603 - val_accuracy: 0.6506
Epoch 19/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5800 - accuracy: 0.6828 - val_loss: 0.6663 - val_accuracy: 0.6207
Epoch 20/20
16/16 [======

...

16/16 [==============================] - 0s 2ms/step - loss: 0.6113 - accuracy: 0.6482 - val_loss: 0.6245 - val_accuracy: 0.6598
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6153 - accuracy: 0.6482 - val_loss: 0.6220 - val_accuracy: 0.6621
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6169 - accuracy: 0.6462 - val_loss: 0.6248 - val_accuracy: 0.6506
Epoch 18/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6205 - accuracy: 0.6472 - val_loss: 0.6220 - val_accuracy: 0.6644
Epoch 19/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6180 - accuracy: 0.6462 - val_loss: 0.6280 - val_accuracy: 0.6506
Epoch 20/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6151 - accuracy: 0.6581 - val_loss: 0.6247 - val_accuracy: 0.6483
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6707 - accuracy: 0.6077 - val_loss: 0.6164 - val_accuracy: 0.6506
Epoch 2/20
16/16 [========

16/16 [==============================] - 0s 2ms/step - loss: 0.6136 - accuracy: 0.6561 - val_loss: 0.6178 - val_accuracy: 0.6552
Epoch 14/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6104 - accuracy: 0.6591 - val_loss: 0.6250 - val_accuracy: 0.6483
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6059 - accuracy: 0.6739 - val_loss: 0.6172 - val_accuracy: 0.6506
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6148 - accuracy: 0.6561 - val_loss: 0.6202 - val_accuracy: 0.6506
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6204 - accuracy: 0.6551 - val_loss: 0.6222 - val_accuracy: 0.6460
Epoch 18/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6068 - accuracy: 0.6591 - val_loss: 0.6179 - val_accuracy: 0.6506
Epoch 19/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6039 - accuracy: 0.6700 - val_loss: 0.6175 - val_accuracy: 0.6575
Epoch 20/20
16/16 [======

16/16 [==============================] - 0s 2ms/step - loss: 0.6144 - accuracy: 0.6512 - val_loss: 0.6257 - val_accuracy: 0.6414
Epoch 12/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6178 - accuracy: 0.6551 - val_loss: 0.6191 - val_accuracy: 0.6552
Epoch 13/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6064 - accuracy: 0.6690 - val_loss: 0.6197 - val_accuracy: 0.6506
Epoch 14/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6085 - accuracy: 0.6690 - val_loss: 0.6189 - val_accuracy: 0.6598
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6081 - accuracy: 0.6640 - val_loss: 0.6146 - val_accuracy: 0.6575
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6029 - accuracy: 0.6680 - val_loss: 0.6203 - val_accuracy: 0.6575
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6038 - accuracy: 0.6571 - val_loss: 0.6230 - val_accuracy: 0.6529
Epoch 18/20
16/16 [======

16/16 [==============================] - 0s 2ms/step - loss: 0.6070 - accuracy: 0.6729 - val_loss: 0.6150 - val_accuracy: 0.6552
Epoch 10/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6089 - accuracy: 0.6650 - val_loss: 0.6176 - val_accuracy: 0.6552
Epoch 11/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6101 - accuracy: 0.6630 - val_loss: 0.6163 - val_accuracy: 0.6598
Epoch 12/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6088 - accuracy: 0.6571 - val_loss: 0.6142 - val_accuracy: 0.6598
Epoch 13/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6102 - accuracy: 0.6502 - val_loss: 0.6202 - val_accuracy: 0.6483
Epoch 14/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6126 - accuracy: 0.6630 - val_loss: 0.6189 - val_accuracy: 0.6552
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6151 - accuracy: 0.6650 - val_loss: 0.6182 - val_accuracy: 0.6598
Epoch 16/20
16/16 [======

16/16 [==============================] - 0s 2ms/step - loss: 0.6366 - accuracy: 0.6492 - val_loss: 0.6417 - val_accuracy: 0.6483
Epoch 8/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6346 - accuracy: 0.6561 - val_loss: 0.6246 - val_accuracy: 0.6368
Epoch 9/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6253 - accuracy: 0.6542 - val_loss: 0.6188 - val_accuracy: 0.6506
Epoch 10/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6173 - accuracy: 0.6502 - val_loss: 0.6270 - val_accuracy: 0.6368
Epoch 11/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6242 - accuracy: 0.6433 - val_loss: 0.6264 - val_accuracy: 0.6391
Epoch 12/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6290 - accuracy: 0.6621 - val_loss: 0.6201 - val_accuracy: 0.6460
Epoch 13/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6109 - accuracy: 0.6561 - val_loss: 0.6266 - val_accuracy: 0.6414
Epoch 14/20
16/16 [========

In [62]:
genAlgWithoutSimulatedAnnealing(10)

Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6671 - accuracy: 0.6057 - val_loss: 0.6527 - val_accuracy: 0.6184
Epoch 2/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6620 - accuracy: 0.6324 - val_loss: 0.6693 - val_accuracy: 0.6345
Epoch 3/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6453 - accuracy: 0.6413 - val_loss: 0.6299 - val_accuracy: 0.6299
Epoch 4/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6202 - accuracy: 0.6433 - val_loss: 0.6366 - val_accuracy: 0.6207
Epoch 5/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6102 - accuracy: 0.6581 - val_loss: 0.6324 - val_accuracy: 0.6414
Epoch 6/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6108 - accuracy: 0.6680 - val_loss: 0.6304 - val_accuracy: 0.6207
Epoch 7/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6066 - accuracy: 0.6571 - val_loss: 0.6312 - val_accuracy: 0.6345
Epoch 8/20
16/16 [==

16/16 [==============================] - 0s 3ms/step - loss: 0.5787 - accuracy: 0.6927 - val_loss: 0.6672 - val_accuracy: 0.6345
Epoch 20/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5811 - accuracy: 0.6601 - val_loss: 0.6687 - val_accuracy: 0.6391
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6470 - accuracy: 0.6492 - val_loss: 0.6286 - val_accuracy: 0.6483
Epoch 2/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6269 - accuracy: 0.6690 - val_loss: 0.6381 - val_accuracy: 0.6529
Epoch 3/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6161 - accuracy: 0.6700 - val_loss: 0.6338 - val_accuracy: 0.6276
Epoch 4/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6002 - accuracy: 0.6650 - val_loss: 0.6354 - val_accuracy: 0.6414
Epoch 5/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5977 - accuracy: 0.6887 - val_loss: 0.6289 - val_accuracy: 0.6299
Epoch 6/20
16/16 [============

16/16 [==============================] - 0s 2ms/step - loss: 0.6044 - accuracy: 0.6512 - val_loss: 0.6192 - val_accuracy: 0.6529
Epoch 18/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6037 - accuracy: 0.6700 - val_loss: 0.6147 - val_accuracy: 0.6644
Epoch 19/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5993 - accuracy: 0.6472 - val_loss: 0.6166 - val_accuracy: 0.6437
Epoch 20/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5887 - accuracy: 0.6680 - val_loss: 0.6178 - val_accuracy: 0.6621
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6600 - accuracy: 0.6275 - val_loss: 0.7103 - val_accuracy: 0.5908
Epoch 2/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6437 - accuracy: 0.6186 - val_loss: 0.6235 - val_accuracy: 0.6598
Epoch 3/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6081 - accuracy: 0.6482 - val_loss: 0.6395 - val_accuracy: 0.6322
Epoch 4/20
16/16 [==========

16/16 [==============================] - 0s 3ms/step - loss: 0.6107 - accuracy: 0.6591 - val_loss: 0.6240 - val_accuracy: 0.6391
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6141 - accuracy: 0.6532 - val_loss: 0.6269 - val_accuracy: 0.6506
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6147 - accuracy: 0.6561 - val_loss: 0.6270 - val_accuracy: 0.6483
Epoch 18/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6080 - accuracy: 0.6630 - val_loss: 0.6282 - val_accuracy: 0.6460
Epoch 19/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6068 - accuracy: 0.6512 - val_loss: 0.6262 - val_accuracy: 0.6529
Epoch 20/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6104 - accuracy: 0.6640 - val_loss: 0.6268 - val_accuracy: 0.6460
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6610 - accuracy: 0.6186 - val_loss: 0.6472 - val_accuracy: 0.6322
Epoch 2/20
16/16 [========

16/16 [==============================] - 0s 3ms/step - loss: 0.5737 - accuracy: 0.6838 - val_loss: 0.6375 - val_accuracy: 0.6230
Epoch 14/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5845 - accuracy: 0.6798 - val_loss: 0.6310 - val_accuracy: 0.6345
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5700 - accuracy: 0.6887 - val_loss: 0.6336 - val_accuracy: 0.6368
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5754 - accuracy: 0.6739 - val_loss: 0.6515 - val_accuracy: 0.6437
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5706 - accuracy: 0.6848 - val_loss: 0.6413 - val_accuracy: 0.6460
Epoch 18/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5546 - accuracy: 0.7036 - val_loss: 0.6534 - val_accuracy: 0.6299
Epoch 19/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5660 - accuracy: 0.6927 - val_loss: 0.6421 - val_accuracy: 0.6276
Epoch 20/20
16/16 [======

...

16/16 [==============================] - 0s 2ms/step - loss: 0.5882 - accuracy: 0.6858 - val_loss: 0.6071 - val_accuracy: 0.6529
Epoch 16/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5891 - accuracy: 0.6789 - val_loss: 0.6118 - val_accuracy: 0.6667
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5925 - accuracy: 0.6700 - val_loss: 0.6151 - val_accuracy: 0.6575
Epoch 18/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5876 - accuracy: 0.6789 - val_loss: 0.6099 - val_accuracy: 0.6621
Epoch 19/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5802 - accuracy: 0.6868 - val_loss: 0.6116 - val_accuracy: 0.6736
Epoch 20/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5812 - accuracy: 0.6779 - val_loss: 0.6135 - val_accuracy: 0.6713
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6657 - accuracy: 0.6146 - val_loss: 0.6136 - val_accuracy: 0.6644
Epoch 2/20
16/16 [========

16/16 [==============================] - 0s 3ms/step - loss: 0.5990 - accuracy: 0.6680 - val_loss: 0.6055 - val_accuracy: 0.6621
Epoch 14/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5931 - accuracy: 0.6749 - val_loss: 0.6076 - val_accuracy: 0.6575
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5882 - accuracy: 0.6789 - val_loss: 0.6044 - val_accuracy: 0.6552
Epoch 16/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5833 - accuracy: 0.6749 - val_loss: 0.6124 - val_accuracy: 0.6667
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5836 - accuracy: 0.6917 - val_loss: 0.6049 - val_accuracy: 0.6621
Epoch 18/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5847 - accuracy: 0.6828 - val_loss: 0.6044 - val_accuracy: 0.6621
Epoch 19/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5871 - accuracy: 0.6759 - val_loss: 0.6092 - val_accuracy: 0.6621
Epoch 20/20
16/16 [======

16/16 [==============================] - 0s 3ms/step - loss: 0.5980 - accuracy: 0.6690 - val_loss: 0.6066 - val_accuracy: 0.6690
Epoch 12/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5978 - accuracy: 0.6759 - val_loss: 0.6036 - val_accuracy: 0.6575
Epoch 13/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5986 - accuracy: 0.6838 - val_loss: 0.6116 - val_accuracy: 0.6552
Epoch 14/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5933 - accuracy: 0.6789 - val_loss: 0.6040 - val_accuracy: 0.6667
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6001 - accuracy: 0.6729 - val_loss: 0.6058 - val_accuracy: 0.6529
Epoch 16/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5904 - accuracy: 0.6848 - val_loss: 0.6091 - val_accuracy: 0.6782
Epoch 17/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5876 - accuracy: 0.6848 - val_loss: 0.6021 - val_accuracy: 0.6598
Epoch 18/20
16/16 [======

16/16 [==============================] - 0s 2ms/step - loss: 0.6017 - accuracy: 0.6838 - val_loss: 0.6069 - val_accuracy: 0.6644
Epoch 10/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5944 - accuracy: 0.6690 - val_loss: 0.6101 - val_accuracy: 0.6713
Epoch 11/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6027 - accuracy: 0.6690 - val_loss: 0.6047 - val_accuracy: 0.6575
Epoch 12/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5994 - accuracy: 0.6591 - val_loss: 0.6063 - val_accuracy: 0.6506
Epoch 13/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5935 - accuracy: 0.6749 - val_loss: 0.6061 - val_accuracy: 0.6644
Epoch 14/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5958 - accuracy: 0.6670 - val_loss: 0.6115 - val_accuracy: 0.6644
Epoch 15/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5932 - accuracy: 0.6779 - val_loss: 0.6166 - val_accuracy: 0.6644
Epoch 16/20
16/16 [======

16/16 [==============================] - 0s 3ms/step - loss: 0.6090 - accuracy: 0.6739 - val_loss: 0.6075 - val_accuracy: 0.6552
Epoch 8/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6043 - accuracy: 0.6621 - val_loss: 0.6104 - val_accuracy: 0.6621
Epoch 9/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6226 - accuracy: 0.6472 - val_loss: 0.6241 - val_accuracy: 0.6552
Epoch 10/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6022 - accuracy: 0.6828 - val_loss: 0.6119 - val_accuracy: 0.6690
Epoch 11/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6073 - accuracy: 0.6719 - val_loss: 0.6090 - val_accuracy: 0.6437
Epoch 12/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5911 - accuracy: 0.6838 - val_loss: 0.6137 - val_accuracy: 0.6828
Epoch 13/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5899 - accuracy: 0.6818 - val_loss: 0.6122 - val_accuracy: 0.6598
Epoch 14/20
16/16 [========

In [26]:
import itertools

def bruteForceAlg(n):
    numResources = n 
    bestResult = ([True for x in range(numResources)], 0.0)
    numFeatures = n
    lst = [list(i) for i in itertools.product([False, True], repeat=numResources)]
    # skip first element [0,....,0]
    for i in range(1, len(lst)):
        sample = lst[i]
        print(sample)
        accuracy = getModelAccuracy(sample)
        print(accuracy)
        if accuracy > bestResult[1]:
            numFeaturesSample = len([x for x in sample if x])
            bestResult = (sample, accuracy)
            numFeatures = numFeaturesSample
        elif accuracy == bestResult[1]:
            numFeaturesSample = len([x for x in sample if x])
            if numFeaturesSample < numFeatures:
                bestResult = (sample, accuracy)
                numFeatures = numFeaturesSample
                
    print('Solution: {}, accuracy: {}', bestResult[0], bestResult[1])
        
        

In [65]:
bruteForceAlg(10)

[False, False, False, False, False, False, False, False, False, True]
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.7481 - accuracy: 0.4941 - val_loss: 0.7014 - val_accuracy: 0.4920
Epoch 2/20
16/16 [==============================] - 0s 2ms/step - loss: 0.7108 - accuracy: 0.4931 - val_loss: 0.7258 - val_accuracy: 0.5103
Epoch 3/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7109 - accuracy: 0.4911 - val_loss: 0.7091 - val_accuracy: 0.4897
Epoch 4/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7034 - accuracy: 0.5089 - val_loss: 0.7028 - val_accuracy: 0.5080
Epoch 5/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7061 - accuracy: 0.4951 - val_loss: 0.6935 - val_accuracy: 0.5149
Epoch 6/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7115 - accuracy: 0.5138 - val_loss: 0.7030 - val_accuracy: 0.4989
Epoch 7/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7043 - accuracy:

16/16 [==============================] - 0s 3ms/step - loss: 0.6904 - accuracy: 0.5375 - val_loss: 0.7178 - val_accuracy: 0.4897
Epoch 17/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6956 - accuracy: 0.5563 - val_loss: 0.7081 - val_accuracy: 0.4851
Epoch 18/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6929 - accuracy: 0.5514 - val_loss: 0.7199 - val_accuracy: 0.4713
Epoch 19/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6889 - accuracy: 0.5415 - val_loss: 0.7130 - val_accuracy: 0.4667
Epoch 20/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6847 - accuracy: 0.5395 - val_loss: 0.7182 - val_accuracy: 0.4828
0.48275861144065857
[False, False, False, False, False, False, False, True, False, False]
Epoch 1/20
16/16 [==============================] - 1s 8ms/step - loss: 0.7790 - accuracy: 0.4822 - val_loss: 0.7325 - val_accuracy: 0.5241
Epoch 2/20
16/16 [==============================] - 0s 2ms/step - loss: 0.717

16/16 [==============================] - 0s 2ms/step - loss: 0.7019 - accuracy: 0.5237 - val_loss: 0.7093 - val_accuracy: 0.4897
Epoch 12/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6988 - accuracy: 0.5356 - val_loss: 0.7271 - val_accuracy: 0.5126
Epoch 13/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6891 - accuracy: 0.5326 - val_loss: 0.7103 - val_accuracy: 0.4989
Epoch 14/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6926 - accuracy: 0.5435 - val_loss: 0.7190 - val_accuracy: 0.5149
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6891 - accuracy: 0.5435 - val_loss: 0.7047 - val_accuracy: 0.4851
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6934 - accuracy: 0.5336 - val_loss: 0.7138 - val_accuracy: 0.4667
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6902 - accuracy: 0.5504 - val_loss: 0.7029 - val_accuracy: 0.5057
Epoch 18/20
16/16 [======

16/16 [==============================] - 0s 3ms/step - loss: 0.7064 - accuracy: 0.5208 - val_loss: 0.7027 - val_accuracy: 0.5195
Epoch 7/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6995 - accuracy: 0.5010 - val_loss: 0.7049 - val_accuracy: 0.5103
Epoch 8/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6964 - accuracy: 0.5287 - val_loss: 0.6963 - val_accuracy: 0.5310
Epoch 9/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6968 - accuracy: 0.5198 - val_loss: 0.6937 - val_accuracy: 0.5264
Epoch 10/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6975 - accuracy: 0.5237 - val_loss: 0.6978 - val_accuracy: 0.5264
Epoch 11/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6937 - accuracy: 0.5316 - val_loss: 0.6983 - val_accuracy: 0.5034
Epoch 12/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6929 - accuracy: 0.5148 - val_loss: 0.7010 - val_accuracy: 0.5356
Epoch 13/20
16/16 [=========

16/16 [==============================] - 0s 3ms/step - loss: 0.7085 - accuracy: 0.5504 - val_loss: 0.7551 - val_accuracy: 0.5011
Epoch 3/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7044 - accuracy: 0.5504 - val_loss: 0.7046 - val_accuracy: 0.4920
Epoch 4/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7043 - accuracy: 0.5346 - val_loss: 0.7071 - val_accuracy: 0.5149
Epoch 5/20
16/16 [==============================] - 0s 3ms/step - loss: 0.7019 - accuracy: 0.5247 - val_loss: 0.7181 - val_accuracy: 0.5011
Epoch 6/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6929 - accuracy: 0.5395 - val_loss: 0.7084 - val_accuracy: 0.4782
Epoch 7/20
16/16 [==============================] - 0s 3ms/step - loss: 0.6919 - accuracy: 0.5395 - val_loss: 0.7170 - val_accuracy: 0.5057
Epoch 8/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6937 - accuracy: 0.5464 - val_loss: 0.7089 - val_accuracy: 0.4805
Epoch 9/20
16/16 [=============

...

16/16 [==============================] - 0s 2ms/step - loss: 0.5922 - accuracy: 0.6779 - val_loss: 0.6170 - val_accuracy: 0.6575
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5888 - accuracy: 0.6858 - val_loss: 0.6157 - val_accuracy: 0.6506
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5925 - accuracy: 0.6680 - val_loss: 0.6302 - val_accuracy: 0.6345
Epoch 18/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5755 - accuracy: 0.7016 - val_loss: 0.6183 - val_accuracy: 0.6483
Epoch 19/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5778 - accuracy: 0.6927 - val_loss: 0.6285 - val_accuracy: 0.6437
Epoch 20/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5764 - accuracy: 0.6976 - val_loss: 0.6272 - val_accuracy: 0.6506
0.6505746841430664
[True, True, True, True, True, True, False, True, False, True]
Epoch 1/20
16/16 [==============================] - 0s 8ms/step - loss: 0.6672 - acc

16/16 [==============================] - 0s 2ms/step - loss: 0.5707 - accuracy: 0.7055 - val_loss: 0.6446 - val_accuracy: 0.6230
Epoch 12/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5601 - accuracy: 0.6986 - val_loss: 0.6421 - val_accuracy: 0.6529
Epoch 13/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5624 - accuracy: 0.6966 - val_loss: 0.6358 - val_accuracy: 0.6437
Epoch 14/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5476 - accuracy: 0.7075 - val_loss: 0.6469 - val_accuracy: 0.6391
Epoch 15/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5403 - accuracy: 0.7273 - val_loss: 0.6534 - val_accuracy: 0.6322
Epoch 16/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5413 - accuracy: 0.7263 - val_loss: 0.6537 - val_accuracy: 0.6299
Epoch 17/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5341 - accuracy: 0.7164 - val_loss: 0.6515 - val_accuracy: 0.6506
Epoch 18/20
16/16 [======

16/16 [==============================] - 0s 2ms/step - loss: 0.5938 - accuracy: 0.6868 - val_loss: 0.6368 - val_accuracy: 0.6368
Epoch 8/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5776 - accuracy: 0.6907 - val_loss: 0.6399 - val_accuracy: 0.6184
Epoch 9/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5762 - accuracy: 0.6937 - val_loss: 0.6404 - val_accuracy: 0.6276
Epoch 10/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5702 - accuracy: 0.7075 - val_loss: 0.6513 - val_accuracy: 0.6368
Epoch 11/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5763 - accuracy: 0.6917 - val_loss: 0.6431 - val_accuracy: 0.6368
Epoch 12/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5729 - accuracy: 0.6897 - val_loss: 0.6459 - val_accuracy: 0.6230
Epoch 13/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5541 - accuracy: 0.7095 - val_loss: 0.6440 - val_accuracy: 0.6322
Epoch 14/20
16/16 [========

16/16 [==============================] - 0s 2ms/step - loss: 0.6117 - accuracy: 0.6630 - val_loss: 0.6112 - val_accuracy: 0.6552
Epoch 4/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6023 - accuracy: 0.6709 - val_loss: 0.6094 - val_accuracy: 0.6506
Epoch 5/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5955 - accuracy: 0.6789 - val_loss: 0.6155 - val_accuracy: 0.6552
Epoch 6/20
16/16 [==============================] - 0s 3ms/step - loss: 0.5923 - accuracy: 0.6818 - val_loss: 0.6132 - val_accuracy: 0.6598
Epoch 7/20
16/16 [==============================] - 0s 2ms/step - loss: 0.6008 - accuracy: 0.6700 - val_loss: 0.6221 - val_accuracy: 0.6598
Epoch 8/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5883 - accuracy: 0.6700 - val_loss: 0.6188 - val_accuracy: 0.6460
Epoch 9/20
16/16 [==============================] - 0s 2ms/step - loss: 0.5857 - accuracy: 0.6719 - val_loss: 0.6169 - val_accuracy: 0.6391
Epoch 10/20
16/16 [============

16/16 [==============================] - 0s 2ms/step - loss: 0.5318 - accuracy: 0.7273 - val_loss: 0.6710 - val_accuracy: 0.6230
0.6229885220527649
Solution: {}, accuracy: {} [True, True, False, True, False, False, False, True, False, True] 0.6804597973823547
